In [20]:
import processors
print(processors.__version__)

3.0.3


In [46]:
%reload_ext autoreload
%autoreload 2

In [22]:
from processors import *
from processors.visualization import JupyterVisualizer as viz

API = ProcessorsAPI(port=8881, keep_alive=True)

INFO - Using path given via $PROCESSORS_SERVER
INFO - Using path given via $PROCESSORS_SERVER
INFO - Connection with server established!
INFO - Connection with server established!
INFO - Server version meets recommendations (v3.0.2)
INFO - Server version meets recommendations (v3.0.2)


In [27]:
import os

# abstracts_dir = "/Users/gus/repos/ohsu-hackathon/OHSU_NLP_Hackathon/sentences_and_abstracts/CIViC_abstracts"
abstracts_dir = "/Users/johngiorgi/Documents/Masters/PrototypeWorkflow/OHSU_NLP_Hackathon/sentences_and_abstracts/CIViC_abstracts"
serialized_documents_dir = "sensitivity-and-adverse-outcomes/serialized-abstracts"

def annotate_documents(collection_dir):
    for f in os.listdir(collection_dir):
        file_path = os.path.join(collection_dir, f)
        text = open(file_path).read()
        doc = API.bionlp.annotate(text) 
        # use filename as the doc's id
        doc.id = os.path.splitext(f)[0]
        yield doc

In [28]:
#docs = annotate_documents(abstracts_dir)

In [29]:
def serialize_documents(collection):
    for doc in collection:
        #doc.id = os.path.splitext(doc.id)[0]
        with open("{}.json".format(doc.id), "w") as out_file:
            out_file.write(doc.to_JSON())

In [30]:
#serialize_documents(docs)

In [31]:
import json

def deserialize_doc_collection(serialized_docs_dir):
    for json_file in os.listdir(serialized_docs_dir):
        fpath = os.path.join(serialized_docs_dir, json_file)
        with open(fpath) as infile:
            text = infile.read()
        doc_dict = json.loads(text)
        doc = Document.load_from_JSON(doc_dict)
        # FIXED, but not released (ADD TEST)
        # py-processors v3.0.3 wasn't retrieving the doc id
        doc.id = os.path.splitext(json_file)[0]
        yield doc

In [33]:
abstracts = list(deserialize_doc_collection(serialized_documents_dir))

In [34]:
abstracts[0]

In [92]:
rules = open("rules.yml", "r").read()

def extract_from_collection(collection, rules):
    for doc in collection:
        mentions = API.odin.extract_from_document(doc, rules)
        for m in sorted(mentions, key=lambda x: (x.document.id, x.sentence, x.start), reverse=False):
            yield m

In [68]:
def display_mentions(mentions):
    for m in mentions:
        print(m.document.id)
        viz.display_mention(m)

In [22]:
mentions = list(extract_from_collection(abstracts))

In [ ]:
#API.stop_server()

In [52]:
from utils import *

In [47]:
drugs_file = "sensitivity-and-adverse-outcomes/drugs_one_per_line.txt"

drug_ngram_dist = ngrams_from_file(file_path=drugs_file, nlp_pipeline=API, n=3)

In [36]:
drug_ngram_dist.most_common(10)

[('ib$', 0.01766996106618748),
 ('nib', 0.011979634621144056),
 ('tin', 0.011829889188379754),
 ('ini', 0.010182689427972447),
 ('ne$', 0.004941599281221923),
 ('in$', 0.004492362982929021),
 ('ine', 0.0037436358191075174),
 ('^AZ', 0.0035938903863432167),
 ('mab', 0.0035938903863432167),
 ('ab$', 0.0035938903863432167)]

In [37]:
background_dist = ngrams_from_documents(abstracts, 3)

In [38]:
background_dist.most_common(10)

[('ati', 0.009354241099264748),
 ('ed$', 0.009061760361210498),
 ('^in', 0.008435658737331727),
 ('^,$', 0.008280740368384311),
 ('ion', 0.008142535184468567),
 ('^th', 0.00813482140676164),
 ('^an', 0.007533146745621467),
 ('^.$', 0.007412297561546304),
 ('the', 0.007051678453747546),
 ('ent', 0.006563782013784521)]

In [42]:
updated_dist = diff_distributions(drug_ngram_dist, background_dist)

In [44]:
updated_dist.most_common(20)

[('ib$', 0.02105818953470745),
 ('nib', 0.013901530940008464),
 ('tin', 0.012498913323834984),
 ('ini', 0.01052056272471123),
 ('^AZ', 0.004503283280591713),
 ('ab$', 0.003958260455264961),
 ('mab', 0.003949258576768574),
 ('ne$', 0.0038204287033107138),
 ('AZD', 0.003555006248517944),
 ('uma', 0.003547524902957155),
 ('01$', 0.003395388769272852),
 ('ine', 0.0025408350442973206),
 ('ert', 0.002317071123460459),
 ('GSK', 0.0022778289231944393),
 ('^GS', 0.002259006813611083),
 ('tib', 0.0021428007457486224),
 ('rti', 0.002111664623224701),
 ('ani', 0.0021010260395471518),
 ('oli', 0.0020969342765942488),
 ('^Da', 0.0020675510314970514)]

In [45]:
sum(v for k,v in updated_dist.items())

0.9999999999999918

In [76]:
rules = open("rules.yml", "r").read()

snippet = create_morphological_rule(ngram_dist=updated_dist, label="Drug", top_n=5)
all_rules = "{}\n{}".format(rules, snippet)
print(all_rules)

taxonomy:
    - AdverseOutcome:
      - Disease:
        - Cancer
    - Drug

vars:
    aoTerms: lemma=/^(morbidity|mortality|toxicity)$/
    diseaseTerms: lemma=/^(disease|disorder|infection|inflammation|syndrome)$/
    cancerTerms: lemma=/^(cancer|leukemia|malignancy|metastasis|tumou?r)$/
    drugSuffixes: lemma=/(ib|pab|mab|zole)$/

rules:
    - name: "adverse-outcome-1"
      label: AdverseOutcome
      priority: 1
      type: token
      pattern: |
        # high morbidity
        (?<! [lemma=low]) [${ aoTerms }] |
        # poor prognosis, adverse outcome, etc.
        [lemma=/^(poor)$/] [lemma=/^(outcome|outlook|prognosis)$/] |
        # high risk of X
        [tag=JJ & !lemma=low]? [lemma=/^(risk)$/] (of [tag=/^(JJ|NN)/]+)?

    - name: "cancer-1"
      label: Cancer
      priority: 1
      type: token
      pattern: |
        # malignant, ovarian, breast, etc.
        [tag=/^(JJ|NN)/]*
        (
         # ex. cancer, tumor, etc.
         [ ${ cancerTerms } ] |
         # blas

In [93]:
mentions = extract_from_collection(abstracts, rules=all_rules)

In [94]:
mention_subset = [m for m in mentions if m.matches("Drug")]

In [95]:
len(mention_subset)

3086

In [96]:
{m.foundBy for m in mention_subset}

{'drug-1',
 'machine-generated-drug-1',
 'machine-generated-drug-2',
 'machine-generated-drug-3',
 'machine-generated-drug-4',
 'machine-generated-drug-5'}

In [97]:
for m in mention_subset:
    if "machine-generated" in m.foundBy:
        print(m.foundBy)
        viz.display_mention(m)

machine-generated-drug-3


machine-generated-drug-3


machine-generated-drug-3


machine-generated-drug-3


machine-generated-drug-3


...

machine-generated-drug-4


machine-generated-drug-3


machine-generated-drug-3


machine-generated-drug-3


machine-generated-drug-3
